In [1]:
import pandas as pd
import numpy as np
from datetime import datetime
import plotly_express as px

import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import StandardScaler

from preprocessing import *
from feature_engineering import *


device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [2]:
df = pd.read_csv("E-Building_Data.csv")
df['date_time'] = pd.to_datetime(df['date_time'])

In [3]:
fe = FeatureEngineering(df) # helper class for feature enginerring
df = fe.feature_engineering(n=False, categorical_features=["season", "room_number"])

In [4]:
latitude = 49.0069
longitude = 8.4037
start_date = datetime(2022, 6, 2)
end_date = datetime(2023, 9, 30)
wf = WeatherFetcher(latitude, longitude, start_date, end_date) # helper class to fetch weather
df = wf.combine_weather(df)

In [5]:
df.columns

Index(['date_time', 'tmp', 'hum', 'tmp_diff', 'hour_sin', 'hour_cos',
       'day_of_week_sin', 'day_of_week_cos', 'month_sin', 'month_cos',
       'season_autumn', 'season_spring', 'season_summer', 'season_winter',
       'room_number_e001', 'room_number_e002', 'room_number_e003',
       'room_number_e004', 'room_number_e010', 'room_number_e101',
       'room_number_e102', 'room_number_e103', 'room_number_e104',
       'room_number_e106', 'room_number_e109', 'room_number_e113',
       'room_number_e201', 'room_number_e203', 'room_number_e206',
       'room_number_e208', 'room_number_e213', 'room_number_e301',
       'room_number_e302', 'room_number_e303', 'room_number_e304',
       'room_number_e305', 'room_number_e306', 'room_number_e311',
       'room_number_eu02', 'room_number_eu07', 'room_number_eu08',
       'room_number_eu09', 'temp', 'dwpt', 'rhum', 'prcp', 'snow', 'wdir',
       'wspd', 'wpgt', 'pres', 'tsun', 'coco'],
      dtype='object')

In [6]:
df_vanilla = df.drop(['season_autumn', 'season_spring', 'season_summer', 'season_winter','temp', 'dwpt', 'rhum', 'prcp', 'snow', 'wdir',
       'wspd', 'wpgt', 'pres', 'tsun', 'coco'], axis=1)
df_seasons = df.drop(['temp', 'dwpt', 'rhum', 'prcp', 'snow', 'wdir',
       'wspd', 'wpgt', 'pres', 'tsun', 'coco'], axis=1)
df_weather = df.drop(['season_autumn', 'season_spring', 'season_summer', 'season_winter'], axis=1)
df_combined = df

In [7]:
def sliding_window_forecast(data: pd.DataFrame, label_name: str, n_in: int, n_out: int, dropna: bool = True) -> pd.DataFrame:
    """
    Transforms time series data into a supervised learning format for forecasting.

    Parameters:
    - data (pd.DataFrame): The input time series data.
    - label_name (str): The name of the target column to forecast.
    - n_in (int): Number of lag observations (input sequence length).
    - n_out (int): Number of future observations to forecast (output sequence length).
    - dropna (bool): Whether to drop rows with NaN values.

    Returns:
    - pd.DataFrame: The transformed DataFrame suitable for forecasting.
    """
    if label_name not in data.columns:
        raise ValueError(f"label_name '{label_name}' is not a column in the data")

    cols, names = list(), list()

    # Input sequence (t-n, ..., t-1, t)
    for i in range(n_in, -1, -1):
        cols.append(data.shift(i))
        names += [f"{col}(t-{i})" if i > 0 else f"{col}(t)" for col in data.columns]

    # Forecast sequence (t+1, ..., t+n)
    for i in range(1, n_out + 1):
        cols.append(data[[label_name]].shift(-i))
        names += [f"{label_name}(t+{i})"]

    # Combine all columns
    data_reframed = pd.concat(cols, axis=1)
    data_reframed.columns = names

    if dropna:
        data_reframed.dropna(inplace=True)

    return data_reframed

In [8]:
dataframes = [df_vanilla, df_seasons, df_weather, df_combined]
[df.set_index("date_time", inplace=True) for df in dataframes]

[None, None, None, None]

In [9]:
dataframes = [df_vanilla, df_seasons, df_weather, df_combined]
transformed_dataframes = [sliding_window_forecast(df, "tmp", 1, 1) for df in dataframes] # forecarst the next datapoint with the previous datapoint
df_vanilla, df_seasons, df_weather, df_combined = transformed_dataframes

In [10]:
def prepare_data(df):
    input_data = df.drop(["tmp(t+1)"], axis=1).values
    targets = df[["tmp(t+1)"]].values
    T = 1  # Number of timesteps to look while predicting
    D = input_data.shape[1]  # Dimensionality of the input
    N = len(input_data) - T

    # Train size: 80% of the total data size
    train_size = int(len(input_data) * 0.80)

    # Normalization of the inputs
    scaler = StandardScaler()
    scaler.fit(input_data[:train_size + T - 1])
    input_data = scaler.transform(input_data)

    # Preparing X_train and y_train
    X_train = np.zeros((train_size, T, D))
    y_train = np.zeros((train_size, 1))

    for t in range(train_size):
        X_train[t, :, :] = input_data[t:t+T]
        y_train[t] = (targets[t+T])

    # Preparing X_test and y_test
    X_test = np.zeros((N - train_size, T, D))
    y_test = np.zeros((N - train_size, 1))

    for i in range(N - train_size):
        t = i + train_size
        X_test[i, :, :] = input_data[t:t+T]
        y_test[i] = (targets[t+T])

    # Convert to torch tensors
    X_train = torch.from_numpy(X_train.astype(np.float32))
    y_train = torch.from_numpy(y_train.astype(np.float32))
    X_test = torch.from_numpy(X_test.astype(np.float32))
    y_test = torch.from_numpy(y_test.astype(np.float32))

    return X_train, y_train, X_test, y_test

In [11]:
class LSTM(nn.Module):
    def __init__(self, input_dim, hidden_dim, layer_dim, output_dim):
        super(LSTM, self).__init__()
        self.M = hidden_dim
        self.L = layer_dim

        self.lstm = nn.LSTM(
            input_size=input_dim,
            hidden_size=hidden_dim,
            num_layers=layer_dim,
            batch_first=True)
        
        self.dropout = nn.Dropout(p=0.5)
        self.fc = nn.Linear(hidden_dim, output_dim)

    def forward(self, X):
        # Check if X is batched or unbatched
        if len(X.shape) == 2:  # Unbatched input: (sequence_length, input_dim)
            X = X.unsqueeze(0)  # Add batch dimension: (1, sequence_length, input_dim)

        batch_size = X.size(0)

        # Initialize hidden state and cell state
        h0 = torch.zeros(self.L, batch_size, self.M).to(X.device)  # (num_layers, batch_size, hidden_dim)
        c0 = torch.zeros(self.L, batch_size, self.M).to(X.device)  # (num_layers, batch_size, hidden_dim)

        # Forward pass through LSTM
        out, (hn, cn) = self.lstm(X, (h0.detach(), c0.detach()))

        # Apply dropout
        out = self.dropout(out)

        # Get output from the last time step
        out = self.fc(out[:, -1, :])
        return out

### Uncomment this cell, if u want to train the models takes about 60min for all 4 models.

In [12]:
# from torch.utils.data import DataLoader, TensorDataset

# def train(model, learning_rate, X_train, y_train, X_test, y_test, batch_size=64, epochs=100):

    
#     criterion = torch.nn.MSELoss()
#     optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
    
#     train_losses = []
#     test_losses = []
    
    
#     train_dataset = TensorDataset(X_train, y_train)
#     train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=False, num_workers=2)
    
    
#     test_dataset = TensorDataset(X_test, y_test)
#     test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=2)
    
#     for epoch in range(epochs):
#         model.train()
        
#         epoch_train_loss = 0.0
#         for batch_X, batch_y in train_loader:
#             optimizer.zero_grad()
            
#             # Forward pass
#             outputs = model(batch_X)
#             loss = criterion(outputs, batch_y)
            
#             # Backward pass and optimization
#             loss.backward()
#             optimizer.step()
            
#             epoch_train_loss += loss.item()
        
#         # Compute average training loss for the epoch
#         train_loss = epoch_train_loss / len(train_loader)
#         train_losses.append(train_loss)
        
#         # Compute test loss
#         model.eval()
#         epoch_test_loss = 0.0
#         with torch.no_grad():
#             for batch_X, batch_y in test_loader:
#                 test_outputs = model(batch_X)
#                 loss = criterion(test_outputs, batch_y)
#                 epoch_test_loss += loss.item()
        
#         # Compute average test loss for the epoch
#         test_loss = epoch_test_loss / len(test_loader)
#         test_losses.append(test_loss)
        
#         if (epoch + 1) % 10 == 0 or epoch == 0:
#             print(f'Epoch [{epoch+1}/{epochs}], Train Loss: {train_loss:.4f}, Test Loss: {test_loss:.4f}')
    
#     return train_losses, test_losses



# dataframes = [df_vanilla, df_seasons, df_weather, df_combined]
# for i, df in enumerate(dataframes, start=0):
#     X_train, y_train, X_test, y_test = prepare_data(df)
# # Define the LSTM model
#     input_size = X_train.shape[2]  # shape of D, input data
#     hidden_size = 64
#     layer_size = 1
#     output_size = 1
#     model = LSTM(input_size, hidden_size, layer_size, output_size)
        
#     # Train the model for the current floor
#     learning_rate = 0.001
#     epochs = 40
#     batch_size = 32
#     train_losses, test_losses = train(model, learning_rate, X_train, y_train, X_test, y_test, epochs=epochs, batch_size=batch_size)
    
#     # Save the trained model and losses
#     torch.save(model.state_dict(), f'lstm_model{i}.pth')
#     with open(f'model{i}_losses.txt', 'w') as file:
#         file.write("Train Losses:\n")
#         for loss in train_losses:
#             file.write(f"{loss}\n")
#         file.write("\nTest Losses:\n")
#         for loss in test_losses:
#             file.write(f"{loss}\n")
    
#     print(f'Model {i} trained, saved, and losses recorded.')

In [14]:
dataframes = [df_vanilla, df_seasons, df_weather, df_combined]

# Process each dataframe and print the shape
input_data_list = []
for i, df in enumerate(dataframes):
    input_data = df.drop(["tmp(t+1)"], axis=1)
    input_data_list.append(input_data)
    print(f"Shape of input_data{i+1}: {input_data.shape}") # depending of number of rooms in each floor

Shape of input_data1: (185102, 74)
Shape of input_data2: (185102, 82)
Shape of input_data3: (185078, 96)
Shape of input_data4: (185078, 104)


In [15]:
# Directory where the models are stored
model_dir = "trained_models"

# Model details
model_details = [
    {"path": "lstm_model0.pth", "input_size": 74},
    {"path": "lstm_model1.pth", "input_size": 82},
    {"path": "lstm_model2.pth", "input_size": 96},
    {"path": "lstm_model3.pth", "input_size": 104},
]

models = []
for details in model_details:
    path = os.path.join(model_dir, details["path"])  # Add directory to the path
    input_size = details["input_size"]
    hidden_size = 64
    num_layers = 1
    output_size = 1

    # Instantiate and load the model
    model = LSTM(input_size, hidden_size, num_layers, output_size)
    model.load_state_dict(torch.load(path))
    model.eval()
    models.append(model)

model_vanilla, model_seasons, model_weather, model_combined = models[:4]

In [16]:
models = [model_vanilla, model_seasons, model_weather, model_combined]
dataframes = [df_vanilla, df_seasons, df_weather, df_combined]

results = {
    'True Values': [],
    'Vanilla Predictions': [],
    'Seasons Predictions': [],
    'Weather Predictions': [],
    'Combined Predictions': []
}

# Iterate over each model and dataframe
for model_name, (df, model) in zip(['Vanilla', 'Seasons', 'Weather', 'Combined'], zip(dataframes, models)):
    X_train, y_train, X_test, y_test = prepare_data(df)

    # Determine device
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)
    X_test = X_test.to(device)
    y_test = y_test.to(device)

    # Set model to evaluation mode
    model.eval()

    # Perform prediction
    with torch.no_grad():
        y_pred = model(X_test)

    y_pred = y_pred.cpu().numpy()
    y_test = y_test.cpu().numpy()

    # Update the results dictionary
    if model_name == 'Vanilla':
        results['True Values'].extend(y_test.flatten())
    results[f'{model_name} Predictions'].extend(y_pred.flatten())

# Debug statement to check lengths of arrays
print("Lengths of arrays in the results dictionary:")
for key, value in results.items():
    print(f"{key}: {len(value)}")

# Ensure all arrays have the same length before creating DataFrame
min_length = min(len(value) for value in results.values())

# Trim all arrays to the same length
for key in results:
    results[key] = results[key][:min_length]

# Convert results dictionary to DataFrame
df_results = pd.DataFrame(results)

Lengths of arrays in the results dictionary:
True Values: 37020
Vanilla Predictions: 37020
Seasons Predictions: 37020
Weather Predictions: 37015
Combined Predictions: 37015


In [115]:
df_plot = df_results[:1000] # dataframe for presentation

In [17]:
import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Scatter(x=df_results.index, y=df_results['True Values'], mode='lines', name='True Values'))
fig.add_trace(go.Scatter(x=df_results.index, y=df_results['Vanilla Predictions'], mode='lines', name='Vanilla Predictions'))
fig.add_trace(go.Scatter(x=df_results.index, y=df_results['Seasons Predictions'], mode='lines', name='Seasons Predictions'))
fig.add_trace(go.Scatter(x=df_results.index, y=df_results['Weather Predictions'], mode='lines', name='Weather Predictions'))
fig.add_trace(go.Scatter(x=df_results.index, y=df_results['Combined Predictions'], mode='lines', name='Combined Predictions'))


fig.update_layout(title='Vorhersage der Temperatur t+1 mit und ohne Wetter/Jahreszeiten',
                  xaxis_title='Index',
                  yaxis_title='Values')

# Show the plot
fig.show()

In [18]:
from sklearn.metrics import mean_squared_error, mean_absolute_error

# Calculate performance metrics for each model
metrics = {}
for model_name in ['Vanilla Predictions', 'Seasons Predictions', 'Weather Predictions', 'Combined Predictions']:
    true_values = df_results['True Values']
    predictions = df_results[model_name]
    
    mse = mean_squared_error(true_values, predictions)
    mae = mean_absolute_error(true_values, predictions)
    
    metrics[model_name] = {'MSE': mse, 'MAE': mae}

# Print performance metrics
for model_name, metric_vals in metrics.items():
    print(f"Model: {model_name}")
    print(f"MSE: {metric_vals['MSE']:.4f}")
    print(f"MAE: {metric_vals['MAE']:.4f}")

Model: Vanilla Predictions
MSE: 3.0598
MAE: 1.3688
Model: Seasons Predictions
MSE: 2.1587
MAE: 1.1446
Model: Weather Predictions
MSE: 3.0409
MAE: 1.3554
Model: Combined Predictions
MSE: 2.6802
MAE: 1.2914
